In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import geopandas as gpd
import contextily as cx
from shapely.geometry import Point
import geoplot.crs as gcrs
import geoplot as gplt
import pyproj
from tqdm import tqdm
from collections import defaultdict
from shapely.geometry import LineString
import networkx as nx
import geopandas as gpd
from scipy.spatial import distance
from shapely.geometry import Point, box
from shapely.geometry import Polygon
import matplotlib.patches as mpatches
from shapely.geometry import LineString
import numpy as np
import json
from pyproj import Transformer

In [ ]:
streets = gpd.read_file('train_dataset_codd_train/vector/Streets_исходные.shp')
humon_road = streets[streets['Foot'] == 1]

In [ ]:
%%time
gdf = gpd.read_file('train_dataset_codd_train/vector/Дома_исходные.shp')
# cell_size = 5000 # размер клетки в метрах
# minx, miny, maxx, maxy = gdf.total_bounds
# grid_cells = []
# for x in np.arange(minx, maxx, cell_size):
#     for y in np.arange(miny, maxy, cell_size):
#         grid_cells.append(Polygon([(x, y), (x + cell_size, y), (x + cell_size, y + cell_size), (x, y + cell_size)]))
# grid = gpd.GeoDataFrame(geometry=grid_cells)
# gdf = gdf[gdf.within(grid.iloc[15].geometry)]
# humon_road = humon_road[humon_road.within(grid.iloc[15].geometry)]
pesh_road = humon_road[humon_road['ROAD_CATEG'] == 'Пешеходные дорожки']


In [ ]:
%%time
school_gdf = gdf[gdf['Purpose'] == 'Школа']
metro_gdf = gdf[gdf['Purpose'] == 'Метро']
hospital_gdf = gdf[gdf['Purpose'] == 'Медицинское учреждение']
sadik_gdf =  gdf[gdf['Purpose'] == 'Детский сад, ясли']
House_data = gdf[(gdf['Purpose'] == "Жилой дом") | (gdf['Purpose'] == "Таунхаус") | (gdf['Purpose'] == "Коттедж") | (gdf['Purpose'] == "Частный дом") | (gdf['Purpose'] == 'Дома_новостройки')]
House_data['Apartments'] = House_data['Apartments'].fillna(1)

In [ ]:
%%time
housePnt = [(House_data.iloc[i]['geometry'].centroid.x, House_data.iloc[i]['geometry'].centroid.y) for i in range(len(House_data))]
HumonCnt = [House_data.iloc[i]['Apartments'] * 3 for i in range(len(House_data))]
school_Pnt = [(school_gdf.iloc[i]['geometry'].centroid.x, school_gdf.iloc[i]['geometry'].centroid.y) for i in range(len(school_gdf))]
metro_Pnt =[(metro_gdf.iloc[i]['geometry'].centroid.x, metro_gdf.iloc[i]['geometry'].centroid.y) for i in range(len(metro_gdf))]
hospital_Pnt = [(hospital_gdf.iloc[i]['geometry'].centroid.x, hospital_gdf.iloc[i]['geometry'].centroid.y) for i in range(len(hospital_gdf))]
sadik_Pnt = [(sadik_gdf.iloc[i]['geometry'].centroid.x, sadik_gdf.iloc[i]['geometry'].centroid.y) for i in range(len(sadik_gdf))]

In [ ]:
%%time
def createGraph(humon_road):
    G = nx.Graph()
    for idx, row in humon_road.iterrows():
        geometry = row['geometry']
        if isinstance(geometry, LineString) and row['Foot'] == 1:
            coords = list(geometry.coords)
            for i in range(len(coords) - 1):
                start = coords[i]
                end = coords[i + 1]
                if row['RoadDirect'] == 'F':
                    G.add_edge(start, end, weight='weight')
                elif row['RoadDirect'] == 'T':
                    G.add_edge(end, start, weight='weight')
                elif row['RoadDirect'] == 'Any':
                    G.add_edge(start, end, weight='weight')
                    G.add_edge(end, start, weight='weight')
    return G                

In [ ]:
%%time
def find_nearest_nodes(Humonroads, points):
    nearest_nodes = []
    buffer_size = 100
    for point in tqdm(points):
        min_dist = float('inf')
        minx = point[0] - buffer_size / 2
        miny = point[1] - buffer_size / 2
        maxx = point[0] + buffer_size / 2
        maxy = point[1] + buffer_size / 2
        square = box(minx, miny, maxx, maxy)
        roads_in_square = Humonroads[Humonroads.intersects(square)]
        graph = createGraph(roads_in_square)
        for node in graph.nodes:
            dist = distance.euclidean(point, node)  
            if dist < min_dist:
                min_dist = dist
                nearest_node = node
        
        nearest_nodes.append(nearest_node)
    
    return nearest_nodes

In [ ]:
%%time
G = createGraph(humon_road)
house_nodes = find_nearest_nodes(humon_road, housePnt)
school_nodes = find_nearest_nodes(humon_road, school_Pnt)
metro_nodes = find_nearest_nodes(humon_road, metro_Pnt)
sadik_nodes = find_nearest_nodes(humon_road, sadik_Pnt)
hospital_nodes = find_nearest_nodes(humon_road, hospital_Pnt)

In [ ]:
%%time
def find_nearest_build_for_houses(residential_houses, schools):
    house_to_school = defaultdict(list)

    for house in residential_houses:
        distances = distance.cdist([house], schools, 'euclidean').flatten()
        nearest_school_idx = np.argmin(distances)
        nearest_school = tuple(schools[nearest_school_idx])
        house_to_school[nearest_school].append(tuple(house))

    return house_to_school

# Применяем функцию



In [ ]:
%%time
nearest_schools_dict = find_nearest_build_for_houses(house_nodes, school_nodes)
nearest_metro_dict = find_nearest_build_for_houses(house_nodes, metro_nodes)
nearest_sadik_dict = find_nearest_build_for_houses(house_nodes, sadik_nodes)
nearest_hospital_dict = find_nearest_build_for_houses(house_nodes, hospital_nodes)

In [ ]:
%%time
paths = []
for i in (nearest_metro_dict.keys()):
    for j in (nearest_metro_dict[i]):
        try:
            paths.append(nx.shortest_path(G, j, i))
        except:
            continue
for i in (nearest_schools_dict.keys()):
    for j in (nearest_schools_dict[i]):
        try:
            paths.append(nx.shortest_path(G, j, i))
        except:
            continue
for i in (nearest_sadik_dict.keys()):
    for j in (nearest_sadik_dict[i]):
        try:
            paths.append(nx.shortest_path(G, j, i))
        except:
            continue
for i in (nearest_hospital_dict.keys()):
    for j in (nearest_hospital_dict[i]):
        try:
            paths.append(nx.shortest_path(G, j, i))
        except:
            continue

In [3]:
# %%time

# G = nx.Graph()
# G_pesh = nx.Graph()

# def add_edge_to_graph(geometry, G):
#     coords = list(geometry.coords)
#     for i in range(len(coords) - 1):
#         G.add_edge(coords[i], coords[i + 1], weight=1, usage=0)  # usage — для подсчёта проходимости

# for geom in humon_road.geometry:
#     if isinstance(geom, LineString):
#         add_edge_to_graph(geom, G)
#     elif geom.geom_type == 'MultiLineString':
#         for part in geom:
#             add_edge_to_graph(part, G)

# for geom in pesh_road.geometry:
#     if isinstance(geom, LineString):
#         add_edge_to_graph(geom, G_pesh)
#     elif geom.geom_type == 'MultiLineString':
#         for part in geom:
#             add_edge_to_graph(part, G_pesh)

# for pat in tqdm(paths):
#     cnt = HumonCnt[house_nodes.index(pat[0])]
#     for i in range(len(pat) - 1):
#         u, v = pat[i], pat[i + 1]
#         if G.has_edge(u, v) and not(G_pesh.has_edge(u, v)):
#             if pat[len(pat)-1] in metro_nodes:
#                 G[u][v]["usage"] += (cnt * 0.45)/4/8000
#             if pat[len(pat)-1] in school_nodes or pat[len(pat)-1] in sadik_nodes:
#                 G[u][v]["usage"] += (cnt * 0.20 * 1.3)/4/8000
#             if pat[len(pat)-1] in hospital_nodes:
#                 G[u][v]["usage"] += (cnt * 0.05)/4/8000
#         if G_pesh.has_edge(u, v):
#             if pat[len(pat)-1] in metro_nodes:
#                 G[u][v]["usage"] += (cnt * 0.45) /4/800
#             if pat[len(pat)-1] in school_nodes or pat[len(pat)-1] in sadik_nodes:
#                 G[u][v]["usage"] += (cnt * 0.20 * 1.3)/4/800
#             if pat[len(pat)-1] in hospital_nodes:
#                 G[u][v]["usage"] += (cnt * 0.05)/4/800

fig, ax = plt.subplots(figsize=(100, 100))


school_gdf.plot(ax=ax, color='blue', alpha=0.5)
metro_gdf.plot(ax=ax, color='orange', alpha=0.5)
hospital_gdf.plot(ax=ax, color='red', alpha=0.5)
sadik_gdf.plot(ax=ax, color='magenta', alpha=0.5)
House_data.plot(ax=ax, color='gray', alpha=0.5)



# Отображение рёбер с цветовой градацией по проходимости
for u, v, data in G.edges(data=True):
    usage = data["usage"]
    if(usage > 0):
        color = (min(1.0, 0 + (usage)),max(0.0, 1 - (usage)),0)  # Цветовая шкала
        line = LineString([u, v])
        ax.plot(*line.xy, color=color, linewidth=5)
    else:
        line = LineString([u, v])
        ax.plot(*line.xy, color='gray', linewidth=2)

building_patch = mpatches.Patch(color='gray', label='жилые дома')
school_patch = mpatches.Patch(color='blue', label='Школы')
hospital_patch = mpatches.Patch(color='orange', label='Метро')
sadik_patch = mpatches.Patch(color='red', label='Больницы')
metro_patch = mpatches.Patch(color='magenta', label='Садики')
# humon_road_df_patch = mpatches.Patch(color='orange', label='Пешеходные дорожки')
ax.legend(handles=[building_patch, school_patch, hospital_patch,sadik_patch, metro_patch], title="Тип объекта", loc="upper right", fontsize="large", title_fontsize="x-large")

plt.title("Проходимость рёбер в путях")
plt.savefig('hitmap.png')
plt.show()

C:\Users\olegt\AppData\Local\Temp\ipykernel_16008\2513632309.py:48: UserWarning: The GeoDataFrame you are attempting to plot is empty. Nothing has been displayed.
  metro_gdf.plot(ax=ax, color='orange', alpha=0.5)
C:\Users\olegt\AppData\Local\Temp\ipykernel_16008\2513632309.py:49: UserWarning: The GeoDataFrame you are attempting to plot is empty. Nothing has been displayed.
  hospital_gdf.plot(ax=ax, color='red', alpha=0.5)


In [ ]:
transformer = Transformer.from_crs("EPSG:3857", "EPSG:4326", always_xy=True)

In [ ]:
JsonSaver = {}
JsonSaver['type'] = "FeatureCollection"
JsonSaver['features'] = []

In [ ]:
for u, v, data in G.edges(data=True):
    point_coords = transformer.transform(u[0], u[1])
    transformed_coords1 = [point_coords[1], point_coords[0]]
    point_coords1 = transformer.transform(v[0], v[1])
    transformed_coords2 = [point_coords1[1], point_coords1[0]]
    usage = data["usage"]
    if(usage > 0):
        a = {}
        a['type'] = 'Feature'
        a['properties'] = {
                    'id': 1,
                    'stage': 1,
                    'name': 'улица 1'}
        a['geometry'] = {
                    'type' : "LineString",
                    'coordinates': [transformed_coords1, transformed_coords2],
                    'color' : [min(1.0, 0 + (usage)),max(0.0, 1 - (usage)),0]
                }
        JsonSaver['features'].append(a)
    else:
        a = {}
        a['type'] = 'Feature'
        a['properties'] = {
                    'id': 1,
                    'stage': 1,
                    'name': 'улица 1'}
        a['geometry'] = {
                    'type' : "LineString",
                    'coordinates': [transformed_coords1, transformed_coords2],
                    'color' : [0.5,0.5,0.5]
                }
        JsonSaver['features'].append(a)
                

In [ ]:
with open('data.json', 'w') as f:
    f.write(json.dumps(JsonSaver))

In [ ]:
%%time
paths = defaultdict(list)
for i in (nearest_metro_dict.keys()):
    for j in tqdm(nearest_metro_dict[i]):
        try:
            paths[(i,j)] = [p for p in nx.all_shortest_paths(G, j, i)]
        except:
            continue
for i in (nearest_schools_dict.keys()):
    for j in tqdm(nearest_schools_dict[i]):
        try:
            paths[(i,j)] = [p for p in nx.all_shortest_paths(G, j, i)]
        except:
            continue
for i in (nearest_sadik_dict.keys()):
    for j in tqdm(nearest_sadik_dict[i]):
        try:
            paths[(i,j)] = [p for p in nx.all_shortest_paths(G, j, i)]
        except:
            continue
for i in (nearest_hospital_dict.keys()):
    for j in tqdm(nearest_hospital_dict[i]):
        try:
            paths[(i,j)] = [p for p in nx.all_shortest_paths(G, j, i)]
        except:
            continue

In [ ]:
%%time
from shapely.geometry import LineString
import numpy as np

G = nx.Graph()
G_pesh = nx.Graph()

def add_edge_to_graph(geometry, G):
    coords = list(geometry.coords)
    for i in range(len(coords) - 1):
        G.add_edge(coords[i], coords[i + 1], weight=1, usage=0)

for geom in humon_road.geometry:
    if isinstance(geom, LineString):
        add_edge_to_graph(geom, G)
    elif geom.geom_type == 'MultiLineString':
        for part in geom:
            add_edge_to_graph(part, G)

for geom in pesh_road.geometry:
    if isinstance(geom, LineString):
        add_edge_to_graph(geom, G_pesh)
    elif geom.geom_type == 'MultiLineString':
        for part in geom:
            add_edge_to_graph(part, G_pesh)
            

for j in tqdm(paths.keys()):
    cnt = HumonCnt[house_nodes.index(j[1])]
    for pat in paths[j]:
        for i in range(len(pat) - 1):
            u, v = pat[i], pat[i + 1]
            if G.has_edge(u, v) and not(G_pesh.has_edge(u, v)):
                if pat[len(pat)-1] in metro_nodes:
                    G[u][v]["usage"] += (cnt / (len(paths[j])) * 0.45)/4/8000
                if pat[len(pat)-1] in school_nodes or pat[len(pat)-1] in sadik_nodes:
                    G[u][v]["usage"] += (cnt / (len(paths[j])) * 0.15 * 1.15)/4/8000
                if pat[len(pat)-1] in hospital_nodes:
                    G[u][v]["usage"] += (cnt / (len(paths[j])) * 0.05)/4/8000
            if G_pesh.has_edge(u, v):
                if pat[len(pat)-1] in metro_nodes:
                    G[u][v]["usage"] += (cnt / (len(paths[j])) * 0.45)/4/800
                if pat[len(pat)-1] in school_nodes or pat[len(pat)-1] in sadik_nodes:
                    G[u][v]["usage"] += (cnt / (len(paths[j])) * 0.15 * 1.15)/4/800
                if pat[len(pat)-1] in hospital_nodes:
                    G[u][v]["usage"] += (cnt / (len(paths[j])) * 0.05)/4/800



fig, ax = plt.subplots(figsize=(100, 100))


school_gdf.plot(ax=ax, color='blue', alpha=0.5)
metro_gdf.plot(ax=ax, color='orange', alpha=0.5)
hospital_gdf.plot(ax=ax, color='red', alpha=0.5)
sadik_gdf.plot(ax=ax, color='magenta', alpha=0.5)
House_data.plot(ax=ax, color='gray', alpha=0.5)



# Отображение рёбер с цветовой градацией по проходимости
for u, v, data in G.edges(data=True):
    usage = (data["usage"])
    if(usage > 0):
        color = (min(1.0, 0 + (usage)),max(0.0, 1 - (usage)),0)  # Цветовая шкала
        line = LineString([u, v])
        ax.plot(*line.xy, color=color, linewidth=5)
    else:
        line = LineString([u, v])
        ax.plot(*line.xy, color='gray', linewidth=2)

building_patch = mpatches.Patch(color='gray', label='жилые дома')
school_patch = mpatches.Patch(color='blue', label='Школы')
hospital_patch = mpatches.Patch(color='orange', label='Метро')
sadik_patch = mpatches.Patch(color='red', label='Больницы')
metro_patch = mpatches.Patch(color='magenta', label='Садики')
# humon_road_df_patch = mpatches.Patch(color='orange', label='Пешеходные дорожки')
ax.legend(handles=[building_patch, school_patch, hospital_patch,sadik_patch, metro_patch], title="Тип объекта", loc="upper right", fontsize="large", title_fontsize="x-large")

plt.title("Проходимость рёбер в путях")
plt.savefig('OptimizerHitmap.png')
plt.show()